<a href="https://colab.research.google.com/github/sihyeon3523/Six_of_cells/blob/modeling/lyricModelling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<br>
<br>

# 0. Install & import libraries 

In [ ]:
from IPython.display import clear_output 

!pip install transformers==4.8.2
!pip install sentencepiece==0.1.96
!pip install tensorflow_addons

clear_output()

import sklearn
import tensorflow
import transformers
import tensorflow_addons

print(sklearn.__version__) # 1.0.2 
print(tensorflow.__version__) # 2.8.0  
print(transformers.__version__) # 4.8.2  
print(tensorflow_addons.__version__) # 0.16.1 

import sentencepiece

import pandas as pd
import numpy as np

import os
import re
import pickle 
import dill # for saving a function as a file(.pkl)
import logging # for changing the tf's logging level
import urllib.request
from tqdm import tqdm

from sklearn import model_selection
from sklearn.metrics import accuracy_score

import tensorflow as tf
import tensorflow_addons as tfa # for using Rectified-Adam optimizer (instead of Adam optimizer) 
from tensorflow.keras import layers, initializers, losses, optimizers, metrics, callbacks 

import transformers
from transformers import TFBertModel # BertTokenizer 제외

import sentencepiece as spm
import ast  # str list to list

1.0.2
2.8.0
4.8.2
0.17.0


In [ ]:
# Random seed 고정
tf.random.set_seed(1234)
np.random.seed(1234)

# Transformers logging level 변경 (WARNING -> ERROR) @ https://huggingface.co/transformers/main_classes/logging.html
transformers.logging.set_verbosity(transformers.logging.ERROR)

# Tensorflow logging level 변경 
tf.get_logger().setLevel(logging.ERROR)

In [ ]:
#KoBERT 불러오기
!git clone https://github.com/monologg/KoBERT-Transformers.git
!mv KoBERT-Transformers/kobert_transformers/tokenization_kobert.py /content
clear_output() # clear the output

#토크나이저 생성
from tokenization_kobert import KoBertTokenizer 

tokenizer = KoBertTokenizer.from_pretrained('monologg/kobert')

# Import Google Drive 

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
os.getcwd()

'/content/drive/My Drive/likelion/proj_fin_seunguk'

In [ ]:
# 경로만 바꾸면 됨!
path = '/content/drive/MyDrive/likelion/proj_fin_seunguk'# google drive project path
data_path = 'colab_data/temp_data/' # model data path
checkpoint_path = 'colab_data/temp_data/saved_models/' # saved model path

os.chdir(path)

# 1. Load the Data

In [ ]:
df_allsongs_original = pd.read_csv('df_allsongs.csv', lineterminator='\n')

In [ ]:
df_allsongs_original.head(3)

Unnamed: 0      Title      Artist        Date       Genre  \
0           0     나의 X에게          경서  2022.04.24         발라드   
1           1       취중고백  김민석 (멜로망스)  2021.12.19         발라드   
2           2  사랑은 늘 도망가         임영웅  2021.10.11  발라드, 국내드라마   

                                               Lyric  \
0  우리 다시 만날래예쁘게 빛나던모든 추억들이너무 그리워너의 품에 안길래이 밤이 새도록...   
1  뭐하고 있었니 늦었지만잠시 나올래너의 집 골목에 있는놀이터에 앉아 있어친구들 만나서...   
2  눈물이 난다 이 길을 걸으면그 사람 손길이 자꾸 생각이 난다붙잡지 못하고 가슴만 떨...   

                                          Lyric_ver2  \
0  <div class="lyric" id="d_video_summary"><!-- h...   
1  <div class="lyric" id="d_video_summary"><!-- h...   
2  <div class="lyric" id="d_video_summary"><!-- h...   

                               preprocess_Lyric_ver2  \
0  우리 다시 만날래 예쁘게 빛나던 모든 추억들이 너무 그리워 너의 품에 안길래 이 밤...   
1  뭐하고 있었니 늦었지만 잠시 나올래 너의 집 골목에 있는 놀이터에 앉아 있어 친구들...   
2  눈물이 난다 이 길을 걸으면 그 사람 손길이 자꾸 생각이 난다 붙잡지 못하고 가슴만...   

                               preprocess_Lyric_ver3  
0  ['우리 다시 만날래', '예쁘게 빛나던', '모든 추억들이', '너무 그리워', ...  
1  ['뭐하고 있었니 늦었지만', '잠시 나올래', '너의 집 골목에 있는', '놀이터...  
2  ['눈물이 난다 이 길을 걸으면', '그 사람 손길이 자꾸 생각이 난다', '붙잡지...

In [ ]:
df_allsongs = df_allsongs_original[["Title", "Artist", "Date", "Genre", "preprocess_Lyric_ver3"]]
df_allsongs

Title         Artist        Date       Genre  \
0            나의 X에게             경서  2022.04.24         발라드   
1              취중고백     김민석 (멜로망스)  2021.12.19         발라드   
2         사랑은 늘 도망가            임영웅  2021.10.11  발라드, 국내드라마   
3            듣고 싶을까  MSG워너비(M.O.M)  2022.02.26         발라드   
4     다정히 내 이름을 부르면           경서예지  2021.05.19         발라드   
...             ...            ...         ...         ...   
3604             애수            진시몬  2004.10.01    성인가요/트로트   
3605     단장의 미아리 고개            송가인  2020.12.26    성인가요/트로트   
3606      어머님 사랑합니다            송가인  2021.05.27    성인가요/트로트   
3607         영동 부르스            송가인  2021.06.13    성인가요/트로트   
3608      일소일소 일노일노            임영웅  2020.04.17    성인가요/트로트   

                                  preprocess_Lyric_ver3  
0     ['우리 다시 만날래', '예쁘게 빛나던', '모든 추억들이', '너무 그리워', ...  
1     ['뭐하고 있었니 늦었지만', '잠시 나올래', '너의 집 골목에 있는', '놀이터...  
2     ['눈물이 난다 이 길을 걸으면', '그 사람 손길이 자꾸 생각이 난다', '붙잡지...  
3     ['우리 함께 듣던 그 노랠 듣고 싶을까', '듣고 나서 잠시 날 생각은 할까', ...  
4     ['끝없이 별빛이 내리던 밤', '기분 좋은 바람이', '두 빰을 스치고', '새벽...  
...                                                 ...  
3604  ['아직도 모르겠어 난 정말 ', '', '꿈이라 생각해야 하는지 ', '', '너...  
3605  ['미아리 눈물고개', '임이 넘던 이별 고개', '화약 연기 앞을 가려', '눈 ...  
3606  ['꽃다운 열아홉에', '연지 찍고 시집와서', '손발이 터지도록', '고생하신 어...  
3607  ['헤어지기 싫어서 애태우던 그 날 밤', '피눈물에 얼룩진 그대의 모습', '어차...  
3608  ['세상사 스무고개 길', '좋은 날만 있을까', '이왕이라면 웃으며 살자', '말...  

[3609 rows x 5 columns]

In [ ]:
print(df_allsongs.info())
print(df_allsongs.describe())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3609 entries, 0 to 3608
Data columns (total 5 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   Title                  3609 non-null   object
 1   Artist                 3609 non-null   object
 2   Date                   3609 non-null   object
 3   Genre                  3609 non-null   object
 4   preprocess_Lyric_ver3  3609 non-null   object
dtypes: object(5)
memory usage: 141.1+ KB
None
       Title Artist        Date Genre  \
count   3609   3609        3609  3609   
unique  3358    947        2042    41   
top       고백    임영웅  2022.05.20    댄스   
freq      10     90          19   486   

                                    preprocess_Lyric_ver3  
count                                                3609  
unique                                               3609  
top     ['우리 다시 만날래', '예쁘게 빛나던', '모든 추억들이', '너무 그리워', ...  
freq                                        

In [ ]:
df_allsongs.preprocess_Lyric_ver3.iloc[12]

"['느낌이 오잖아 ', '떨리고 있잖아', '언제까지 눈치만 볼 거니', '네 맘을 말해봐 ', '딴청 피우지 말란 말이야', '네 맘 가는 그대로 ', '지금 내 손을 잡아', '어서 내 손을 잡아', '우연히 고개를 돌릴 때 마다', '눈이 마주치는 건', '며칠 밤 내내 꿈속에 나타나', '밤새 나를 괴롭히는 건', '그 많은 빈자리 중에서 하필', '내 옆자릴 고르는 건', '나도 모르게 어느새 실없는 웃음', '흘리고 있다는 건', '그럼 말 다했지 뭐', '우리 얘기 좀 할까', '느낌이 오잖아 떨리고 있잖아', '언제까지 눈치만 볼 거니', '네 맘을 말해봐 ', '딴청 피우지 말란 말이야', '네 맘 가는 그대로 ', '지금 내 손을 잡아', '핸드폰 진동에 ', '심장이 덜컥내려 앉는다는 건', '오 나도 모르게 ', '어느새 짓궂은 네 말투', '자꾸 듣고 싶은걸', '어떡해', '저기 멀리 걸어온다', '눈이 마주친다', '언제까지 넌 모른척 할거니', '사랑이 온거야 너와 나 말이야', '네가 좋아 정말 못 견딜 만큼', '그거면 된거야 ', '더는 생각하지 말란 말이야', '네 맘 가는 그대로', '느낌이 오잖아 떨리고 있잖아', '언제까지 눈치만 볼 거니', '네 맘을 말해봐 ', '딴청 피우지 말란 말이야', '네 맘 가는 그대로 ', '지금 내 손을 잡아', '그냥 내 손을 잡아', '지금 내 손을 잡아', ' ', '']"

# Colab 끊겨서 뒷부분 장르 태깅 안되는 경우 방지 all rows shuffle

In [ ]:
df_allsongs = df_allsongs.sample(frac=1).reset_index(drop=True)  # shuffling하고 index reset

# Load saved Model


In [ ]:
# 1) Load the Model-builder (function)
with open(data_path + 'model_BERTfunction_v1.pkl', 'rb') as f:
    create_model = dill.loads(pickle.load(f)) # use dill to pickle a python function

# 2) Load the Bert-tokenizer 
with open(data_path + 'tokenizer-bert.pkl', 'rb') as f:
    tokenizer = pickle.load(f) 


# 3) Create the model & load the Model-weights (from checkpoint file)
resolver = tf.distribute.cluster_resolver.TPUClusterResolver(tpu='grpc://' + os.environ['COLAB_TPU_ADDR'])
tf.config.experimental_connect_to_cluster(resolver) 
tf.tpu.experimental.initialize_tpu_system(resolver)
strategy = tf.distribute.TPUStrategy(resolver) # Obsolete : tf.distribute.experimental.TPUStrategy()

with strategy.scope(): 
    model = create_model(max_length=300) 

model.load_weights(filepath=checkpoint_path + 'best_bert_weights.h5')

INFO:absl:Entering into master device scope: /job:worker/replica:0/task:0/device:CPU:0


Downloading:   0%|          | 0.00/426 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/369M [00:00<?, ?B/s]

# Classifier as a function

In [ ]:
def predict_sentiment_element(sentence, tokenizer, model):
    """
    가사 내 문장 별 확률 값 추출
    """    
    SEQ_LEN = 300 

    # Tokenizing / Tokens to sequence numbers / Padding
    encoded_dict = tokenizer.encode_plus(text=re.sub("[^\s0-9a-zA-Zㄱ-ㅎㅏ-ㅣ가-힣]", "", sentence), # 특수문자 제거
                                         padding='max_length', 
                                         truncation = True,
                                         max_length=SEQ_LEN) 
    
    token_ids = np.array(encoded_dict['input_ids']).reshape(1, -1) 
    token_masks = np.array(encoded_dict['attention_mask']).reshape(1, -1)
    token_segments = np.array(encoded_dict['token_type_ids']).reshape(1, -1)
    
    new_inputs = (token_ids, token_masks, token_segments)

    # Prediction
    pred = model.predict(new_inputs) 
    all_pred_proba = np.round(pred * 100, 2)
    
    #top_pred_proba = np.round(np.max(pred) * 100, 2) 
    #pred_class = ['분노혐오','놀람공포','슬픔','행복'][np.argmax(pred, axis=1)[0]] # 수정하면 4개 클래스 다 나올듯! 
    #print("{}% 확률로 {} 텍스트입니다.".format(top_pred_proba, pred_class))

    return all_pred_proba 

In [ ]:
def predict_sentiment_lyrics(lyrics):
    """
    가사의 감성 확률 값 추출, 문장별 감성 확률의 정규화 평균  
    가사내 문장 단위로 predict_sentiment_element 함수 적용   
    마지막 원소 '' 빈칸임. <br/> 태그 기준으로 split해서 나옴, 빈칸인 element 제거
    """
    lyrics = ast.literal_eval(lyrics) # str list to list
    lyrics = list(filter(lambda x: x != '', lyrics))

    print(len(lyrics)) 
    print(lyrics)


    for i in range(len(lyrics)):
        
        if lyrics[i] != '':
            all_pred_proba = predict_sentiment_element(lyrics[i], tokenizer, model)
            anger = all_pred_proba[0][0]
            scary = all_pred_proba[0][1]
            sad = all_pred_proba[0][2]
            happy = all_pred_proba[0][3]
            #print(i, lyrics[i], all_pred_proba) 

        anger += anger 
        scary += scary
        sad  += sad
        happy += happy

    total_array = np.ndarray.round( (np.array([(anger, scary, sad, happy)]) / (anger + scary + sad + happy)), 2)
    top_pred_prob = total_array[0][np.argmax(total_array, axis=1)[0]]
    top_pred_class = ['분노혐오','놀람공포','슬픔','행복'][np.argmax(total_array, axis=1)[0]]

    return total_array, top_pred_class, top_pred_prob

In [ ]:
# test_list = df_allsongs.preprocess_Lyric_ver3.iloc[35]
# total_array, top_pred_class, top_pred_prob = predict_sentiment_lyrics(test_list)

In [ ]:
# print(total_array) 
# print(top_pred_class)  
# print(top_pred_prob)  

preprocess_Lyric_ver3에 적용 <br> 

list가 str 형태로 row에 저장되었기 때문에 ast library로 다시 list로 바꿔주어야한다.<br>
(str list to list)

# Apply model

In [ ]:
# Emotion = []
# Probability = []
# 분노혐오 = []
# 놀람공포 = []
# 슬픔 = []
# 행복 = []


# for row in tqdm(df_allsongs.iterrows()):


#         total_array, top_pred_class, top_pred_prob = predict_sentiment_lyrics(row[1][-1])
#         Emotion.append(top_pred_class)
#         Probability.append(top_pred_prob)
#         분노혐오.append(total_array[0][0])
#         놀람공포.append(total_array[0][1])
#         슬픔.append(total_array[0][2])
#         행복.append(total_array[0][3]) 

# df_allsongs['Emotion'] = Emotion
# df_allsongs['Proba'] = Probability
# df_allsongs['분노혐오'] = 분노혐오
# df_allsongs['놀람공포'] = 놀람공포
# df_allsongs['슬픔'] = 슬픔
# df_allsongs['행복'] = 행복

# df_allsongs.to_csv('songtagged_may27.csv')

In [ ]:
df_allsongs['Emotion'] = " "
df_allsongs['Probability'] = " "
df_allsongs['분노혐오'] = " "
df_allsongs['놀람공포'] = " "
df_allsongs['슬픔'] = " "
df_allsongs['행복'] = " "

for i in tqdm(df_allsongs.index):
    lyrics = df_allsongs['preprocess_Lyric_ver3'].iloc[i]
    total_array, top_pred_class, top_pred_prob = predict_sentiment_lyrics(lyrics)
    df_allsongs['Emotion'].iloc[i] = top_pred_class 
    df_allsongs['Probability'].iloc[i] = top_pred_prob
    df_allsongs['분노혐오'].iloc[i] = total_array[0][0]
    df_allsongs['놀람공포'].iloc[i] = total_array[0][1]
    df_allsongs['슬픔'].iloc[i] = total_array[0][2]
    df_allsongs['행복'].iloc[i] = total_array[0][3]

    df_allsongs.to_csv('songtagged_may29.csv')

  0%|          | 0/3609 [00:00<?, ?it/s]

97
["I can't understand what people are sayin'", '어느 장단에 맞춰야 될지', '한 발자국 떼면 한 발자국 커지는 shadow', '잠에서 눈을 뜬 여긴 또 어디', '어쩜 서울 또 New York or Paris', '일어나니 휘청이는 몸', 'Look at my feet, look down', '날 닮은 그림자', '흔들리는 건 이놈인가', '아니면 내 작은 발끝인가', '두렵잖을 리 없잖아', '다 괜찮을 리 없잖아', '그래도 I know', '서툴게 I flow', '저 까만 바람과 함께 날아', 'Hey na na na', '미치지 않으려면 미쳐야 해', 'Hey na na na', '나를 다 던져 이 두 쪽 세상에', 'Hey na na na', 'Can’t hold me down cuz you know I’m a fighter', '제 발로 들어온 아름다운 감옥', "Find me and I'm gonna live with ya", '(Eh-oh)', '가져와 bring the pain oh yeah', '(Eh-oh)', '올라타봐 bring the pain oh yeah', "Rain be pourin'", "Sky keep fallin'", 'Everyday oh na na na', '(Eh-oh)', '가져와 bring the pain oh yeah', 'Bring the pain', '모두 내 피와 살이 되겠지', 'Bring the pain', 'No fear, 방법을 알겠으니', '작은 것에 breathe', '그건 어둠 속 내 산소와 빛', '내가 나이게 하는 것들의 힘', '넘어져도 다시 일어나 scream', '넘어져도 다시 일어나 scream', '언제나 우린 그랬으니', '설령 내 무릎이 땅에 닿을지언정', '파묻히지 않는 이상', '그저 그런 해프닝쯤 될 거란 걸', 'Win no matter what', 'Win no matter what', 'Win no matter what', 

INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>]
  0%|          | 1/3609 [01:26<86:48:56, 86.62s/it]

35
['함께 했던 많은 계절이', '봄에 눈이 녹듯 사라진다 해도', '아직 나는 너를 기억해', '세상 무엇보다 빛나던 모습을', '어떤 날도 어떤 말도', '우리 안녕이라 했었던 그 날도', '저기 어딘가에 꿈을 꾸던 시간조차도', '오랜 영화처럼 다시', '빛이 되어 남을테니', '어떤 날도 어떤 말도', '우리 안녕이라 했었던 그 날도', '문득 고갤 드는', '가슴 아픈 기억조차도', '언젠가는 아름다운', '눈물들로 남을테니까', '아직 나는 너를 기억해', '세상 무엇보다 빛나던 모습을', '어떤 날도 어떤 말도', '우리 안녕이라 했었던 그 날도', '저기 어딘가에 꿈을 꾸던 시간조차도', '오랜 영화처럼 다시', '빛이 되어 남을테니', '저기 우리 행복했었던 시간이', '아직도 손에 잡힐 듯', '어딘가 아쉬운 마음도', '때로는 서운한 마음도', '언젠가 함께 했었던 그 약속도', '어떤 날도 어떤 말도', '우리 안녕이라 했었던 그 날도', '문득 고갤 드는', '가슴 아픈 기억조차도', '언젠가는 아름다운', '눈물들로 남을테니까', '함께 했던 많은 계절은', '비록 여기에서 끝이 난다해도']


  0%|          | 2/3609 [01:45<47:08:41, 47.05s/it]

...

35
['이제 난 아무 말 하고 있지 않아요', '내 얘길 하는 것이 너무 지겨워', '나는 그들과 같은 세상을 살고 있는데', '마치 다른 세상에 사는 것처럼 ', '나는 좋은 추억을 갖고 있어요', '한때 정말 행복했던 것 같아요', '눈앞에 쟤처럼 아니 ', '그 애처럼 살고 싶어요', '나는 내가 아닌 것 같아', '샘을 내고 있진 않아요 ', '샘이 좀 나긴 했지만', '부러워하지는 않아요 서운하긴 했지만', '아쉽다 말하라는 것 같아', '미안하다 말하라는 것 같아', '난 아냐 난 아냐', '걘 요즘 어떻게 지낸대', '혹은 누구랑 사귄대 ', '나는 아무렇지 않아요', '그냥 그저 살고 있어요', '난 요즘 생각을 좀 한대', '시끄러 나 살기에도 바쁜데', '내가 불행하길 바란 건지', '날 생각해서 하는 말인지', '나는 그들과 같은 세상을 살고 있는데', '샘을 내고 있진 않아요 ', '샘이 좀 나긴 했지만', '부러워하지는 않아요 서운하긴 했지만', '아쉽다 말하라는 것 같아', '미안하다 말하라는 것 같아', '샘을 내고 있지 않아요', '부러워하지도 않아요', '아쉽다 말하라는 것 같아', '미안하다 말하라는 것 같아', '난 아냐 난 아냐', '난 아냐 난 아냐']


 79%|███████▉  | 2867/3609 [20:29:48<4:00:55, 19.48s/it]

106
['You know who it is', "Coming 'round again ", 'You want a dose of this ', "Right now It's K/DA uh", "I'm a goddess with a blade ", '소리쳐봐 내 이름 잊지 못하게 ', 'Loud loud loud loud ', 'I could take it to the top ', '절대 멈추지 못해 ', '내가 끝내주는 ', 'Bad gal gal gal', 'And when I start to talk like that ', 'like that', "Oh you won't know how to react ", "I'm a picture perfect face ", 'With that wild in my veins ', 'You can hear it in my ', 'Growl growl growl growl ', 'So keep your eyes on me now ', '무엇을 보든 좋아할 거야 ', '닿을 수 없는 level ', '나와 대결 원한 널 확신해 ', 'We gotta it all in our hands now ', 'So can you handle ', "what we're all about ", "We're so tough ", 'Not scared to show you up ', 'Can you feel the rush now ', "Ain't nobody bringing us", 'down down down ', 'down down down ', "They could try but we're gonna ", 'wear the crown ', 'You could go another round ', 'round round round ', 'round round round ', "Wish you luck but you're not ", 'bringing us down ', 'We go hard', 'Till we get it get it ', '

 79%|███████▉  | 2868/3609 [20:30:41<6:08:25, 29.83s/it]

88
['Yeah MC Sniper', '마법의 성으로 그대를 초대', 'oh yeah MC Sniper', 'oh yeah 그대를 초대', "I'm greet U everynight", "I'm magician", '마법의 성으로 hey', '찬바람에 부는 옷깃', '사랑에 빠진 달빛', '눈꽃이 흩날리는', '거리는 온통 잿빛', '물감에 물이 든 듯', '아련히 번지고', '하늘은 장미빛', '무지개를 만들어내죠', 'oh 안녕하세요', "I'm greet U everynight", '귀머거리 꽃들과', '정겹게 나누는 인사', '창가로 날아드는', '새들의 노래가', '사랑이 시작됐다', '내게 말을 하는 듯', '널 사랑하고 널 믿어주는 것', '이것 밖에 더 해줄게 난 없어', '지켜줄게 품에 꼭 안고', '그저 내게 너 하나만 있으면 돼', '별들조차 질투하는', '신비스런 눈동자', '두 팔 벌려 안고 싶은', '가녀린 몸체가', '너무나도 아름다운', '그대를 모두 다', '글로 묘사할 순 없어', ' 그댄 나의 동화', '매일 아침 반복되는', '사랑의 질문과', '영원히 널 지켜줄게', '이게 나의 대답', '보석보다 찬란한', '그대의 모든 걸예찬', '하는 나는 피동피동', '행복의 살이 찐다', '마법의 성 이곳은', '사랑을 피우는 화실', '심술부정 질투와', '행복의 회복실', '집착한 욕심을', '씻어내는 욕실', '이곳엔 없어 가슴 아픈', '이별의 숨바꼭질', '쏟아지는 별을 보며', '사랑의 별점을 치죠', '마법사는 틀린 적 없어', '우린 그걸 믿죠', '사랑의 점성술', '삶이 부리는 심술', '아픔따윈 없는 이 곳', 'oh 마법의 성으로', "oh yeah I'm magician", "oh yeah I'm greet U everynight", 'oh yeah 마법의 성으로', 'oh yeah 그대를 초대', '널 사랑하고 널 믿어주는 것', '이것밖에 더 해줄 게 난 없어', '지켜줄게 품에 꼭 안고', '그저 내